In [1]:
import os
os.environ['TF_ENABLE_ONEDNN_OPTS'] = '0'

from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
!pip install --upgrade flwr

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 598.1/598.1 kB 29.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 98.2/98.2 kB 10.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.2/4.2 MB 89.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 294.9/294.9 kB 27.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.3/2.3 MB 85.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 236.0/236.0 kB 23.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 47.3/47.3 kB 4.4 MB/s eta 0:00:00
  Attempting uninstall: protobuf
    Found existing installation: protobuf 5.29.5
    Uninstalling protobuf-5.29.5:
      Successfully uninstalled protobuf-5.29.5
  Attempting uninstall: click
    Found existing installation: click 8.2.1
    Uninstalling click-8.2.1:
      Successfully uninstalled click-8.2.1
  Attempting uninstall: cryptography
    Found existing installation: cryptography 43.0.3
    Uninstalling cryptography-43.0.3:
      S

In [3]:
!pip install -U "flwr[simulation]"

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 66.7/66.7 MB 34.5 MB/s eta 0:00:00


In [1]:
%cd /content/drive/MyDrive/Colab Notebooks/
!ls *.py

/content/drive/MyDrive/Colab Notebooks
client.py      dataset.py	     main.py   server_contribution.py
cnn_models.py  main_contribution.py  model.py  server.py


In [2]:
import torch
print("GPU available:", torch.cuda.is_available())
print("Device name:", torch.cuda.get_device_name(0) if torch.cuda.is_available() else "CPU only")

GPU available: True
Device name: NVIDIA A100-SXM4-40GB


# main_contribution.py

In [ ]:
%%writefile "/content/drive/MyDrive/Colab Notebooks/main_contribution.py"

import sys
sys.path.append('/content/drive/MyDrive/Colab Notebooks')

import os
from flwr.simulation import start_simulation
from client import FlowerClient
from flwr.server import ServerConfig
from server_contribution import get_eval_fn, CustomFedAvg

# Paths
DATA_BASE = "/content/drive/MyDrive/Colab Notebooks/Covid19-dataset/splits"
LOG_DIR = "/content/drive/MyDrive/Colab Notebooks/logs/contribution_logs"
os.makedirs(LOG_DIR, exist_ok=True)

# Get clients (with optional exclusion)
def get_clients(model_name, split_name, exclude_client_id=None):
    clients = []
    for i in range(3):
        if exclude_client_id is not None and i == exclude_client_id:
            continue
        data_path = os.path.join(DATA_BASE, split_name, f"Client-{i+1}")
        clients.append(FlowerClient(model_name, data_path, i, split_name))
    return clients

# Run FL for baseline or excluded client
def run_simulation(model_name, split_name, exclude_client_id=None, custom_tag=""):
    clients = get_clients(model_name, split_name, exclude_client_id)
    tag = custom_tag if custom_tag else split_name
    eval_fn = get_eval_fn(model_name, tag, clients, split_name)

    strategy = CustomFedAvg(
        eval_fn=eval_fn,
        fraction_fit=1.0,
        fraction_evaluate=1.0,
        min_fit_clients=len(clients),
        min_evaluate_clients=len(clients),
        min_available_clients=len(clients)
    )

    def client_fn(cid: str):
        return clients[int(cid)]

    start_simulation(
        client_fn=client_fn,
        num_clients=len(clients),
        config=ServerConfig(num_rounds=10),
        strategy=strategy
    )

# CLI entry
if __name__ == "__main__":
    if len(sys.argv) != 4:
        print("Usage: python main_contribution.py <model_name> <split_name> contribution")
        sys.exit(1)

    model = sys.argv[1].lower()
    split = sys.argv[2]
    mode = sys.argv[3].lower()

    if mode == "contribution":
        print("🔁 Running baseline FL with all clients...")
        run_simulation(model, split, exclude_client_id=None, custom_tag="with_all")

        for cid in range(3):
            print(f"🚫 Running FL excluding client {cid}...")
            run_simulation(model, split, exclude_client_id=cid, custom_tag=f"excl_client_{cid}")

# server_contribution.py

In [ ]:
%%writefile "/content/drive/MyDrive/Colab Notebooks/server_contribution.py"

import os
import csv
import flwr as fl

LOG_DIR = "/content/drive/MyDrive/Colab Notebooks/logs/contribution_logs"

def get_eval_fn(model_name, tag, clients, split_name):
    def evaluate(server_round, parameters, config):
        total_correct, total_samples = 0, 0
        round_logs = []

        for i, client in enumerate(clients):
            loss, num_samples, metrics = client.evaluate(parameters, config)
            acc = metrics.get("accuracy", 0.0)
            total_correct += acc * num_samples
            total_samples += num_samples
            round_logs.append([server_round, i, acc, loss])

        # Log client-level accuracy
        log_client_path = f"{LOG_DIR}/log_client_metrics_{model_name}_{tag}_{split_name}.csv"
        with open(log_client_path, "a", newline="") as f:
            writer = csv.writer(f)
            if os.stat(log_client_path).st_size == 0:
                writer.writerow(["round", "client_id", "accuracy", "loss"])
            writer.writerows(round_logs)

        # Log global accuracy
        global_acc = total_correct / total_samples if total_samples > 0 else 0.0
        log_global_path = f"{LOG_DIR}/log_global_metrics_{model_name}_{tag}_{split_name}.csv"
        with open(log_global_path, "a", newline="") as f:
            writer = csv.writer(f)
            if os.stat(log_global_path).st_size == 0:
                writer.writerow(["round", "global_accuracy"])
            writer.writerow([server_round, global_acc])

        return 0.0, {"accuracy": global_acc}

    return evaluate

class CustomFedAvg(fl.server.strategy.FedAvg):
    def __init__(self, eval_fn, **kwargs):
        super().__init__(**kwargs)
        self._eval_fn_custom = eval_fn

    def evaluate(self, server_round, parameters, config=None):
        if config is None:
            config = {}
        config["server_round"] = server_round
        config["server_side"] = True
        return self._eval_fn_custom(server_round, parameters, config)

# Label_skew

In [ ]:
!python main_contribution.py tinycnn Label_skew contribution

2025-07-08 07:25:40.105811: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751959540.126711    1221 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751959540.133032    1221 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 07:25:40.153767: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py simplecnn Label_skew contribution

2025-07-08 07:57:49.564644: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751961469.586341   15613 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751961469.592875   15613 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 07:57:49.614829: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py resnet18 Label_skew contribution

2025-07-08 08:32:00.968070: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751963520.989074   30152 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751963520.995461   30152 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 08:32:01.016598: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

In [ ]:
!python main_contribution.py mobilenetv2 Label_skew contribution

2025-07-08 09:11:13.869498: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751965873.891064   46027 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751965873.897495   46027 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 09:11:13.918467: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

# Concept_shift

In [ ]:
!python main_contribution.py tinycnn Concept_shift contribution

2025-07-08 09:48:47.617261: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751968127.638517   61436 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751968127.644988   61436 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 09:48:47.666051: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py simplecnn Concept_shift contribution

2025-07-08 10:17:28.105292: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751969848.129359   74781 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751969848.136036   74781 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 10:17:28.156915: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py resnet18 Concept_shift contribution

2025-07-08 10:51:03.578475: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751971863.599775   89149 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751971863.606227   89149 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 10:51:03.627124: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

In [ ]:
!python main_contribution.py mobilenetv2 Concept_shift contribution

2025-07-08 11:29:50.501110: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751974190.522566  104908 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751974190.529062  104908 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 11:29:50.550438: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

# Feature_skew

In [ ]:
!python main_contribution.py tinycnn Feature_skew contribution

2025-07-08 12:07:54.425115: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751976474.446403  120435 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751976474.452831  120435 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 12:07:54.473978: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py simplecnn Feature_skew contribution

2025-07-08 12:38:13.139321: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751978293.160997  134231 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751978293.167548  134231 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 12:38:13.188895: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py resnet18 Feature_skew contribution

2025-07-08 13:12:40.236411: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751980360.257531  148841 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751980360.263918  148841 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 13:12:40.284925: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

In [ ]:
!python main_contribution.py mobilenetv2 Feature_skew contribution

2025-07-08 13:52:29.136831: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751982749.158189  164877 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751982749.164665  164877 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 13:52:29.185654: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

# Pathological

In [12]:
!python main_contribution.py tinycnn Pathological contribution

2025-07-09 14:28:06.504198: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 14:28:06.522443: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752071286.543749  182993 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752071286.550280  182993 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 14:28:06.571708: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [13]:
!python main_contribution.py simplecnn Pathological contribution

2025-07-09 15:05:03.470659: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 15:05:03.488209: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752073503.509486  199385 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752073503.515931  199385 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 15:05:03.537298: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [14]:
!python main_contribution.py resnet18 Pathological contribution

2025-07-09 15:44:57.985973: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 15:44:58.003586: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752075898.024883  214963 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752075898.031334  214963 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 15:44:58.052517: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [15]:
!python main_contribution.py mobilenetv2 Pathological contribution

2025-07-09 16:31:02.208738: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 16:31:02.226203: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752078662.247707  232107 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752078662.254164  232107 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 16:31:02.275326: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

# Dirichlet_label

In [ ]:
!python main_contribution.py tinycnn Dirichlet_label contribution

2025-07-08 15:35:33.980187: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751988934.001814  196330 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751988934.008342  196330 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 15:35:34.029694: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py simplecnn Dirichlet_label contribution

2025-07-08 16:54:57.469545: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751993697.490742  229383 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751993697.497316  229383 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 16:54:57.519004: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
	Instead, use the `flwr run` CLI command to start a local simul

In [ ]:
!python main_contribution.py resnet18 Dirichlet_label contribution

2025-07-08 17:47:00.572512: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1751996820.594138  247982 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1751996820.600594  247982 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-08 17:47:00.622021: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
🔁 Running baseline FL with all clients...
/usr/local/lib/python3.11/dist-packages/torchvision/models/_uti

In [3]:
!python main_contribution.py mobilenetv2 Dirichlet_label contribution

2025-07-09 06:19:29.886472: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 06:19:29.903718: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752041969.924257    5013 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752041969.930577    5013 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 06:19:29.951345: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

# Quantity_skew

In [4]:
!python main_contribution.py tinycnn Quantity_skew contribution

2025-07-09 07:26:43.253923: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 07:26:43.271082: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752046003.292483   28734 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752046003.299167   28734 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 07:26:43.320650: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [5]:
!python main_contribution.py simplecnn Quantity_skew contribution

2025-07-09 08:08:40.469100: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 08:08:40.487239: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752048520.509632   45488 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752048520.516501   45488 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 08:08:40.537619: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [6]:
!python main_contribution.py resnet18 Quantity_skew contribution

2025-07-09 08:49:55.805268: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 08:49:55.823035: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752050995.844826   61783 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752050995.851404   61783 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 08:49:55.873160: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [7]:
!python main_contribution.py mobilenetv2 Quantity_skew contribution

2025-07-09 09:38:42.139229: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 09:38:42.156451: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752053922.177359   80059 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752053922.183817   80059 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 09:38:42.204713: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

# IID_equal

In [8]:
!python main_contribution.py tinycnn IID_equal contribution

2025-07-09 11:18:45.721609: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 11:18:45.739523: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752059925.761271  111403 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752059925.767837  111403 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 11:18:45.789177: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [9]:
!python main_contribution.py simplecnn IID_equal contribution

2025-07-09 11:54:36.329944: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 11:54:36.347492: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752062076.369071  126568 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752062076.375477  126568 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 11:54:36.396753: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [10]:
!python main_contribution.py resnet18 IID_equal contribution

2025-07-09 12:28:43.637031: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 12:28:43.654323: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752064123.675473  140993 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752064123.681966  140993 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 12:28:43.702811: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

In [11]:
!python main_contribution.py mobilenetv2 IID_equal contribution

2025-07-09 13:08:25.520280: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-07-09 13:08:25.537776: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1752066505.559201  156894 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1752066505.565686  156894 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2025-07-09 13:08:25.586815: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instr

# Runner code

In [ ]:
import subprocess
from tqdm import tqdm

models = ["tinycnn", "simplecnn", "resnet18", "mobilenetv2"]
splits = ["Label_skew", "Concept_shift", "Feature_skew", "Pathological",
          "Quantity_skew", "IID_equal", "Dirichlet_label"]

# Each combination runs 4 simulations: with_all + excl_0 + excl_1 + excl_2
total_runs = len(models) * len(splits)

with tqdm(total=total_runs, desc="Running contribution evaluations") as pbar:
    for split in splits:
        for model in models:
            tqdm.write(f"\n▶️ Running: {model} on {split} [Contribution Mode]")
            subprocess.run(["python", "main_contribution.py", model, split, "contribution"])
            pbar.update(1)